Before running the code below a postgres database of the MIMIC data has to be created as described here: https://github.com/MIT-LCP/mimic-code

In [1]:
import pandas as pd
pd.set_option('display.max_rows', 100)
pd.set_option('display.max_columns', 500)

pd.set_option('display.width', 1000)
import numpy as np
import time
import datetime
import i2bmi
import pickle
from pandas.core.tools.datetimes import _guess_datetime_format_for_array
from pandas.plotting import register_matplotlib_converters
register_matplotlib_converters()
import warnings
import itertools
from itertools import product

import matplotlib.pyplot as plt

import os
import pandasql as ps

from scipy import stats

import torch
import utils_paper as u

import I2_Sepsis

i2bmi.jupyter_widen()

In [2]:
from sqlalchemy import create_engine
# Postgres username, password, and database name
POSTGRES_ADDRESS = '127.0.0.1' ## INSERT YOUR DB ADDRESS
POSTGRES_PORT = '5432' ## INSERT YOUR PORT (DEFAULT IS 5432)
POSTGRES_USERNAME = 'wendland' ## INSERT YOUR POSTGRES USERNAME
POSTGRES_PASSWORD = '8c2oV00a' ## INSERT YOUR POSTGRES PASSWORD
POSTGRES_DBNAME = 'mimiciv'  ## INSERT YOUR POSTGRES DATABASE NAME


# A long string that contains the necessary Postgres login information
postgres_str = ('postgresql://{username}:{password}@{ipaddress}:{port}/{dbname}'.format(username=POSTGRES_USERNAME,password=POSTGRES_PASSWORD,ipaddress=POSTGRES_ADDRESS,port=POSTGRES_PORT,dbname=POSTGRES_DBNAME))

# Create the connection
cnx = create_engine(postgres_str)

In [7]:
sql_scripts=u.sql_queries_start()

In [ ]:
data = u.load_dfs(sql_scripts,cnx)

loading adt...

In [27]:
#FINALIZE DATAFRAMES
lvdf = data['lvdf'].copy()
adt = u.make_adt(data['adt'],data['icu_adt'])
vasodf = data['vasodf'].copy()
dxdf = data['dxdf'].copy()
mvdf = data['mvdf'].copy()
abxdf = data['abxdf'].copy()
cxdf = data['cxdf'].copy()
demo = data['demo'].copy()
Sepsis3_key = data['Sepsis3'].copy()
uo = data['uo'].copy()

### Map Columns to Data Model

In [ ]:
names_to_standard = {
            'subject_id' : 'patient_id', 
            'hadm_id' : 'encounter_id', 
            'admittime' : 'admit_time', 
            'dischtime' : 'discharge_time',
            'adt_loc': 'location',
            'intime_hr': 'location_start',
            'outtime_hr':'location_end',
        
            
            
            'val' : 'value', 
            'mark' : 'label', 
            'time' : 'time_measured', 
            
            
            'vent_start': 'vent_start',
            'vent_end':'vent_end',
            'ventilation_status': 'vent_type',
            
            
            'vaso_start': 'vaso_start',
            'vaso_end': 'vaso_end',
            'rate_uom': 'vaso_units',
            'rate': 'vaso_dose',
            'drug': 'pressor_name',
            

            'starttime':'abx_start',
            'stoptime': 'abx_end',
            'antibiotic' : 'antibiotic_name',
            
            
            'charttime': 'culture_time',
            'spec_type_desc': 'culture_type',
    
            'icd_code' : 'dx_code',
            'recorded_date' : 'dx_time',
    
            'uo_time':'uo_time'
       }

In [10]:
dfs=[lvdf, adt, vasodf, dxdf, mvdf, abxdf, cxdf, demo , Sepsis3_key , uo]
for df in dfs:
    df.rename(columns=names_to_standard,inplace=True)
    display(df.head())
# DROP COLUMNS THAT ARE NOT NEEDED
adt = adt.drop(columns=['admit_time','discharge_time'])
vasodf = vasodf.drop(columns=['encounter_id'])
lvdf = lvdf.drop(columns=['encounter_id'])
mvdf = mvdf.drop(columns=['stay_id'])
abxdf = abxdf.drop(columns=['encounter_id','stay_id'])
cxdf = cxdf.drop(columns=['encounter_id','micro_specimen_id','chartdate','positiveculture'])
uo = uo.drop(columns=['encounter_id'])

In [11]:
display(pd.DataFrame(mvdf['vent_type'].value_counts()))
mvdf = mvdf[mvdf['vent_type'].isin(['InvasiveVent'])].reset_index(drop=True)
mvdf.loc[mvdf['vent_type']=='InvasiveVent','vent_type']='VENT'

vent_type
SupplementalOxygen      65977
InvasiveVent            34800
Tracheostomy             3950
NonInvasiveVent          3826
HFNC                     2530
None                      152

In [12]:
# REMOVE PRESSORS OTHER THAN 'norepinephrine','epinephrine','dopamine','dobutamine' AS THIS WAS THE DECISION MADE BY MIMIC
display(pd.DataFrame(vasodf['pressor_name'].value_counts()))
vasodf = vasodf[vasodf['pressor_name'].isin(['norepinephrine','epinephrine','dopamine','dobutamine'])].reset_index(drop=True)

pressor_name
norepinephrine        335998
phenylephrine         193260
vasopressin            25892
epinephrine            24470
dopamine               16892
dobutamine              8513

In [ ]:
import pickle

with open('D:/Mimic_data/adt.pkl', 'wb') as handle:
    pickle.dump(adt, handle, protocol=pickle.HIGHEST_PROTOCOL)
    
with open('D:/Mimic_data/vasodf.pkl', 'wb') as handle:
    pickle.dump(vasodf, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/dxdf.pkl', 'wb') as handle:
    pickle.dump(dxdf, handle, protocol=pickle.HIGHEST_PROTOCOL)
    
with open('D:/Mimic_data/mvdf.pkl', 'wb') as handle:
    pickle.dump(mvdf, handle, protocol=pickle.HIGHEST_PROTOCOL)
    
with open('D:/Mimic_data/abxdf.pkl', 'wb') as handle:
    pickle.dump(abxdf, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/cxdf.pkl', 'wb') as handle:
    pickle.dump(cxdf, handle, protocol=pickle.HIGHEST_PROTOCOL)
    
with open('D:/Mimic_data/demo.pkl', 'wb') as handle:
    pickle.dump(demo, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/sepsis3_key.pkl', 'wb') as handle:
    pickle.dump(Sepsis3_key, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/uo.pkl', 'wb') as handle:
    pickle.dump(uo, handle, protocol=pickle.HIGHEST_PROTOCOL)
    
with open('D:/Mimic_data/data.pkl', 'wb') as handle:
    pickle.dump(data, handle, protocol=pickle.HIGHEST_PROTOCOL)

### Map lvdf lables to Data Model Lables

In [63]:
# CURRENT LABELS, section had to be runned once
lvdf['label'].value_counts()

rr         6455503
sbp        6355873
map        6352072
spo2       6323768
hr         6323768
cr         3279150
plt        3206162
bun        3186406
wbc        3165749
bicarb     2971532
gcs        1637763
bili       1157773
O2 Flow     585385
pO2         390126
fio2        256382
Name: label, dtype: int64

In [14]:
# MAP CURRENT LABELS TO LABELS REQUIRED BY THE MINIMAL SEPSIS DATA MODEL
lvdf_map = {#'TEMP' : 'temp_c', 
            'HR' : 'hr', 
            'RR' :  'rr',
            #'PCO2': 'pco2_art',
            'WBC' : 'wbc',
            'SBP' : 'sbp',
            'MAP' : 'map',
            #'LACTATE' : 'lactate',
            'Cr' : 'cr',
            'BILI' : 'bili',
            'PLT' : 'plt',
            #'INR' : 'inr',
            #'PT' : 'pt',
            'GCS' : 'gcs',
            'FiO2': 'fio2',
            'O2_Flow': 'O2 Flow',
            'SpO2' : 'spo2',
            'BUN' : 'bun',
            #'PT' : 'pt',
            #'UOP' : np.nan,
            'FiO2' : 'fio2',
            #'pH' : 'ph_art',
            'pO2' : 'pO2',
            #'AaGradient' : np.nan,
            #'Na': 'na',
            #'K' : 'k',
            #'HCT' : 'hcrt',
            #'PTT': 'ptt',
            #'PEEP': 'peep',
            #'PFRatio': np.nan,
            #'SFRatio': np.nan,
           }

inv_map = {v: k for k, v in lvdf_map.items() if pd.notna(k)}

lvdf['label']  = lvdf['label'].map(inv_map)
lvdf['time_measured'] = pd.to_datetime(lvdf['time_measured'],utc=True)
lvdf.drop_duplicates(inplace= True)


lvdf['label'].value_counts()

RR         6455503
SBP        6355873
MAP        6352072
SpO2       6323768
HR         6323768
Cr         3279150
PLT        3206162
BUN        3186406
WBC        3165749
GCS        1637763
BILI       1157773
O2_Flow     585385
pO2         390126
FiO2        256382
Name: label, dtype: int64

In [15]:
# DROP ANY UNKNOWN LABELS
lvdf = lvdf[~lvdf['value'].isna()]

In [16]:
import pickle
with open('D:/Mimic_data/lvdf.pkl', 'wb') as handle:
    pickle.dump(lvdf, handle, protocol=pickle.HIGHEST_PROTOCOL)

### Run Sepsis-3

In [ ]:
cx_final=cxdf
SOI_full, RTI_full, Sep_3,SOI_final,RTI_final = I2_Sepsis.Sepsis_3(lvdf=lvdf, adt=adt, mvdf= mvdf, abxdf = abxdf, cxdf= cx_final, vasodf = vasodf, uodf=uo, demo=demo, SF_dict = {1:512,2:357,3:214,4:89}, calc_FiO2 = False, calc_PF = True, calc_SF= False, 
max_flow_convert= 6, calc_interval_mins = 15, LOCF_hours = None, include_SF_RATIO = False, include_qSOFA =False,mech_vent_def = 'VENT', gcs_cutoff = 15, debug = True, cutoff = 2)
Sep_3_orig,RTI_orig,SOI_orig,MSep_3,MIMIC_SOI,MIMIC_SOFA,Sep_3,RTI,python_SOFA,SOI_trim=cleanup_sep3(Sep_3,RTI_full,SOI_full,data,names_to_standard,cnx)

In [27]:
with open('D:/Mimic_data/RTI.pkl', 'wb') as handle:
    pickle.dump(RTI, handle, protocol=pickle.HIGHEST_PROTOCOL)
    
with open('D:/Mimic_data/python_SOFA.pkl', 'wb') as handle:
    pickle.dump(python_SOFA, handle, protocol=pickle.HIGHEST_PROTOCOL)
    
with open('D:/Mimic_data/SOI_trim.pkl', 'wb') as handle:
    pickle.dump(SOI_trim, handle, protocol=pickle.HIGHEST_PROTOCOL)
    
with open('D:/Mimic_data/MSep_3.pkl', 'wb') as handle:
    pickle.dump(MSep_3, handle, protocol=pickle.HIGHEST_PROTOCOL)
    
with open('D:/Mimic_data/MIMIC_SOI.pkl', 'wb') as handle:
    pickle.dump(MIMIC_SOI, handle, protocol=pickle.HIGHEST_PROTOCOL)
    
with open('D:/Mimic_data/MIMIC_SOFA.pkl', 'wb') as handle:
    pickle.dump(MIMIC_SOFA, handle, protocol=pickle.HIGHEST_PROTOCOL)

### End of OpenSep Pipeline

#### Load icustay,and static data of the Sepsis Patients

In [ ]:
sql_scripts=u.sql_queries_start()

from sqlalchemy import create_engine
# Postgres username, password, and database name
POSTGRES_ADDRESS = '127.0.0.1' ## INSERT YOUR DB ADDRESS
POSTGRES_PORT = '5432' ## INSERT YOUR PORT (DEFAULT IS 5432)
POSTGRES_USERNAME = 'wendland' ## INSERT YOUR POSTGRES USERNAME
POSTGRES_PASSWORD = '8c2oV00a' ## INSERT YOUR POSTGRES PASSWORD
POSTGRES_DBNAME = 'mimiciv'  ## INSERT YOUR POSTGRES DATABASE NAME


# A long string that contains the necessary Postgres login information
postgres_str = ('postgresql://{username}:{password}@{ipaddress}:{port}/{dbname}'.format(username=POSTGRES_USERNAME,password=POSTGRES_PASSWORD,ipaddress=POSTGRES_ADDRESS,port=POSTGRES_PORT,dbname=POSTGRES_DBNAME))

# Create the connection
cnx = create_engine(postgres_str)
emar_sql = '''SELECT * FROM mimiciv_hosp.emar'''
emar=u.load_lab(table=emar_sql,Patients=Sep_3,cnx=cnx,sep_data=Sep_3)
with open('D:/Mimic_data/emar.pkl', 'wb') as handle:
    pickle.dump(emar, handle, protocol=pickle.HIGHEST_PROTOCOL)
icustays_sql = '''SELECT * FROM mimiciv_derived.icustay_detail'''
icustays=u.load_lab(table=icustays_sql,Patients=Sep_3,cnx=cnx,sep_data=Sep_3)
with open('D:/Mimic_data/icustays.pkl', 'wb') as handle:
    pickle.dump(icustays, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [6]:
static=u.load_static(Patients=Sep_3,cnx=cnx)

loading WITH Static AS ((
    SELECT t1.subject_id as patient_id, t1.stay_id, t1.gender, t1.admission_age,t3.height, t2.weight 
    FROM mimiciv_derived.icustay_detail t1 
    FULL OUTER JOIN mimiciv_derived.first_day_weight t2 on t1.stay_id=t2.stay_id
    FULL OUTER JOIN mimiciv_derived.first_day_height t3 on t1.stay_id=t3.stay_id
    ))
    SELECT * FROM static...

In [19]:
static["male"]=0
static["male"][static["gender"]=="M"]=1
static["female"]=0
static["female"][static["gender"]=="F"]=1

C:\Users\wendland\AppData\Local\Temp/ipykernel_12100/2222278922.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  static["male"][static["gender"]=="M"]=1
C:\Users\wendland\AppData\Local\Temp/ipykernel_12100/2222278922.py:4: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  static["female"][static["gender"]=="F"]=1


In [21]:
with open('D:/Mimic_data/static.pkl', 'wb') as handle:
    pickle.dump(static, handle, protocol=pickle.HIGHEST_PROTOCOL)

#### Load covariables

In [11]:
bg_sql, blood_differential_sql, chemistry_sql, cbc_sql, enzyme_sql, vitalsign_sql, lab_rest_sql, lab_demo_sql, lab_demo2_sql, lab_demo3_sql, comorbidites_sql, cr_bl_sql, gcs_sql, kdigo_uo_sql = u.load_sepsis_dat_sql()
lab_bg, lab_blood_differential,lab_chemistry, lab_cbc, lab_crbl, lab_enzyme, lab_gcs, lab_kdigo_uo, lab_vitalsign, lab_rest, lab_demo, lab_demo2, lab_demo3, lab_comorbidities, lab_comp = u.load_sepsis_dat(Patients=Sep_3, cnx=cnx, sep_data=Sep_3)

loading WITH bg AS ((
    SELECT subject_id,charttime as time,storetime,so2 as val, 'so2' as mark, hadm_id
    FROM mimiciv_derived.bg
    WHERE so2 IS NOT NULL
    )
    UNION
    (
    SELECT subject_id,charttime as time,storetime,po2 as val, 'po2' as mark, hadm_id
    FROM mimiciv_derived.bg
    WHERE po2 IS NOT NULL
    )
    UNION
    (
    SELECT subject_id,charttime as time,storetime,pco2 as val, 'pco2' as mark, hadm_id
    FROM mimiciv_derived.bg
    WHERE pco2 IS NOT NULL
    )
    UNION
    (
    SELECT subject_id,charttime as time,storetime,fio2 as val, 'fio2' as mark, hadm_id
    FROM mimiciv_derived.bg
    WHERE fio2 IS NOT NULL
    )
    UNION
    (
    SELECT subject_id,charttime as time,storetime,fio2_chartevents as val, 'fio2_chartevents' as mark, hadm_id
    FROM mimiciv_derived.bg
    WHERE fio2_chartevents IS NOT NULL
    )
    UNION
    (
    SELECT subject_id,charttime as time,storetime,aado2_calc as val, 'aado2_calc' as mark, hadm_id
    FROM mimiciv_derived.bg
 

KeyboardInterrupt: 

In [22]:
with open('D:/Mimic_data/lab_bg.pkl', 'wb') as handle:
    pickle.dump(lab_bg, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/lab_blood_differential.pkl', 'wb') as handle:
    pickle.dump(lab_blood_differential, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/lab_chemistry.pkl', 'wb') as handle:
    pickle.dump(lab_chemistry, handle, protocol=pickle.HIGHEST_PROTOCOL)#
with open('D:/Mimic_data/lab_cbc.pkl', 'wb') as handle:
    pickle.dump(lab_cbc, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/lab_crbl.pkl', 'wb') as handle:
    pickle.dump(lab_crbl, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/lab_enzyme.pkl', 'wb') as handle:
    pickle.dump(lab_enzyme, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/lab_gcs.pkl', 'wb') as handle:
    pickle.dump(lab_gcs, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/lab_kdigo_uo.pkl', 'wb') as handle:
    pickle.dump(lab_kdigo_uo, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/lab_vitalsign.pkl', 'wb') as handle:
    pickle.dump(lab_vitalsign, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/lab_rest.pkl', 'wb') as handle:
    pickle.dump(lab_rest, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/lab_demo.pkl', 'wb') as handle:
    pickle.dump(lab_demo, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/lab_demo2.pkl', 'wb') as handle:
    pickle.dump(lab_demo2, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/lab_demo3.pkl', 'wb') as handle:
    pickle.dump(lab_demo3, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/lab_comorbidities.pkl', 'wb') as handle:
    pickle.dump(lab_comorbidities, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/lab_comp.pkl', 'wb') as handle:
    pickle.dump(lab_comp, handle, protocol=pickle.HIGHEST_PROTOCOL)

#lab_comp describes complete dataset
    

#### Load Antibiotic data and select Antibiotics

Antibiotic Prescriptions

In [13]:
abxdf2_sql = '''SELECT * FROM mimiciv_derived.antibiotic2'''

In [14]:
abx2=u.load_lab(table=abxdf2_sql,Patients=Sep_3,cnx=cnx,sep_data=Sep_3)
abx2=abx2.rename(columns={"subject_id": "patient_id"})

loading SELECT * FROM mimiciv_derived.antibiotic2...(2.7s)


In [15]:
abx2=u.abx_preproc(abx2)

In [67]:
with open('D:/Mimic_data/abx2.pkl', 'wb') as handle:
    pickle.dump(abx2, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [16]:
Sep_3["encounter_id"]=Sep_3["encounter_id"].astype(int)
Sep_3["Sepsis_Time"]=Sep_3["Sepsis_Time"].apply(lambda x:x.tz_localize(None))

In [17]:
abx_g=abx2[abx2["stay_id"].notna()].groupby("antibiotic")

In [18]:
abx_g.nunique().sort_values("hadm_id",ascending=False)

patient_id  hadm_id  stay_id  route  starttime  stoptime  dose_val_rx  dose_unit_rx  doses_per_24_hrs
antibiotic                                                                                                                                
Vancomycin                                13188    14795    15691     12      35549     36126           14             4                 7
CefePIME                                   6414     6944     7195      1      14787     14917            6             3                 4
Piperacillin-Tazobactam                    5533     5937     6137      2      12997     12672            4             3                 5
Cefazolin                                  5603     5687     5761      4       7079      7175            9             3                 5
CefTRIAXone                                5052     5389     5489      3       6942      7022            6             3                 3
MetroNIDAZOLE                              4647     4942     5085      5       6569      6566            7             2                 5
Ciprofloxacin                              3036     3180     3261      6       5166      5364            5             1                 4
Azithromycin                               2432     2590     2622      5       3995      4068            8             2                 2
Levofloxacin                               2183     2296     2326      5       3178      3231            5             1                 2
Meropenem                                  1758     1920     1993      2       4695      4655            5             3                 5
CefTAZidime                                1164     1212     1244      4       2024      2004            8             3                 4
Mupirocin Nasal Ointment 2%                1138     1144     1219      2       1387      1413            1             1                 5
Sulfameth/Trimethoprim                      909     1003     1037      4       1513      1602           72             4                 5
Ampicillin-Sulbactam                        904      915      931      1       1143      1147            2             2                 6
Clindamycin                                 687      692      700      5        908       915            5             1                 4
Ampicillin                                  561      570      578      3        756       760            9             3                 5
Linezolid                                   528      566      589      5       1010      1002            1             1                 4
Gentamicin                                  451      462      469      5        659       663           63             1                 5
Tobramycin                                  441      462      466      2        774       784           65             1                 4
Doxycycline Hyclate                         451      455      461      3        604       617            4             1                 3
Nafcillin                                   354      360      374      1        533       538            3             3                 4
Erythromycin                                285      295      298      4        381       383           11             2                 5
Aztreonam                                   254      258      264      1        484       477            3             1                 4
Amoxicillin-Clavulanic Acid                 196      196      198      3        234       235            3             1                 3
Cephalexin                                  183      184      184      2        205       206            2             1                 4
Cefpodoxime Proxetil                        111      111      111      3        125       125            3             1                 3
Nitrofurantoin                              104      106      106      1        129       131            3             1                 5
Penici

Intravenous administration of Antibiotics

In [ ]:
abxdf3_sql = '''SELECT * FROM mimiciv_icu.inputevents'''
abx3 = u.load_lab(table=abxdf3_sql,Patients=Sep_3,cnx=cnx,sep_data=Sep_3)

abx3 = abx3[abx3["ordercategoryname"].isin(['08-Antibiotics (IV)','09-Antibiotics (Non IV)','Pre Admission/Non-ICU'])]
with open('D:/Mimic_data/abx3.pkl', 'wb') as handle:
    pickle.dump(abx3, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [ ]:
antibiotic_string='Piperacillin-Tazobactam'
antibiotic_id = [225893]
piperacillin_hadms_its_only, piperacillin_stay_list, piperacillin_stay_times = u.patient_stay_search_antibiotic(antibiotic_string=antibiotic_string,antibiotic_id=antibiotic_id,prescriptions=abx2,icu_inputevents=abx3,icustays=icustays)

with open('D:/Mimic_data/piperacillin_hadms_its_only.pkl', 'wb') as handle:
    pickle.dump(piperacillin_hadms_its_only, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/piperacillin_stay_list.pkl', 'wb') as handle:
    pickle.dump(piperacillin_stay_list, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/piperacillin_stay_times.pkl', 'wb') as handle:
    pickle.dump(piperacillin_stay_times, handle, protocol=pickle.HIGHEST_PROTOCOL)

Number of Patients treated only with Piperacillin/Tazobactam

In [26]:
len(piperacillin_hadms_its_only)

280

90-days mortality rate for Piperacillin/Tazobactam

In [28]:
sum(demo[demo["encounter_id"].astype(int).isin(piperacillin_hadms_its)]["discharge_time"].apply(np.datetime64)>(demo[demo["encounter_id"].astype(int).isin(piperacillin_hadms_its)]["dod"].apply(np.datetime64)-np.timedelta64(90,'D')))/len(piperacillin_hadms_its)

0.46446615021892895

In [57]:
antibiotic_string='Vancomycin'
antibiotic_id = [225798]
vancomycin_hadms_its_only, vancomycin_stay_list, vancomycin_stay_times = u.patient_stay_search_antibiotic(antibiotic_string=antibiotic_string,antibiotic_id=antibiotic_id,prescriptions=abx2,icu_inputevents=abx3,icustays=icustays)

with open('D:/Mimic_data/vancomycin_hadms_its_only.pkl', 'wb') as handle:
    pickle.dump(vancomycin_hadms_its_only, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/vancomycin_stay_list.pkl', 'wb') as handle:
    pickle.dump(vancomycin_stay_list, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/vancomycin_stay_times.pkl', 'wb') as handle:
    pickle.dump(vancomycin_stay_times, handle, protocol=pickle.HIGHEST_PROTOCOL)

Number of Patients treated only with Vancomycin

In [59]:
len(vancomycin_hadms_its_only)

1021

90-days mortality rate for Vancomycin

In [61]:
sum(demo[demo["encounter_id"].astype(int).isin(vancomycin_hadms_its)]["discharge_time"].apply(np.datetime64)>(demo[demo["encounter_id"].astype(int).isin(vancomycin_hadms_its)]["dod"].apply(np.datetime64)-np.timedelta64(90,'D')))/len(vancomycin_hadms_its)

0.4063936198972695

In [ ]:
antibiotic_string='CefTRI'
antibiotic_id = [225855]
Ceftri_hadms_its_only, Ceftri_stay_list, Ceftri_stay_times = u.patient_stay_search_antibiotic(antibiotic_string=antibiotic_string,antibiotic_id=antibiotic_id,prescriptions=abx2,icu_inputevents=abx3,python_SOFA=python_SOFA,icustays=icustays)

with open('D:/Mimic_data/Ceftri_hadms_its_only.pkl', 'wb') as handle:
    pickle.dump(Ceftri_hadms_its_only, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/Ceftri_stay_list.pkl', 'wb') as handle:
    pickle.dump(Ceftri_stay_list, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/Ceftri_stay_times.pkl', 'wb') as handle:
    pickle.dump(Ceftri_stay_times, handle, protocol=pickle.HIGHEST_PROTOCOL)

Number of Patients treated only with Ceftriaxone

In [90]:
len(Ceftri_hadms_its_only)

1144

90-days mortality rate for Ceftriaxone

In [259]:
sum(demo[demo["encounter_id"].astype(int).isin(CefTRI_hadms_its)]["discharge_time"].apply(np.datetime64)>(demo[demo["encounter_id"].astype(int).isin(CefTRI_hadms_its)]["dod"].apply(np.datetime64)-np.timedelta64(90,'D')))/len(CefTRI_hadms_its)

0.35572462423455187

In [ ]:
antibiotic_string='Cefe'
antibiotic_id = [225851]
Cefe_hadms_its_only, Cefe_stay_list, Cefe_stay_times = u.patient_stay_search_antibiotic(antibiotic_string=antibiotic_string,antibiotic_id=antibiotic_id,prescriptions=abx2,icu_inputevents=abx3,icustays=icustays)

with open('D:/Mimic_data/Cefe_hadms_its_only.pkl', 'wb') as handle:
    pickle.dump(Cefe_hadms_its_only, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/Cefe_stay_list.pkl', 'wb') as handle:
    pickle.dump(Cefe_stay_list, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/Cefe_stay_times.pkl', 'wb') as handle:
    pickle.dump(Cefe_stay_times, handle, protocol=pickle.HIGHEST_PROTOCOL)

Number of Patients treated only with Cefepime

In [6]:
len(Cefe_hadms_its_only)

133

90-days mortality rate for Cefepime

In [14]:
sum(demo[demo["encounter_id"].astype(int).isin(Cefe_hadms_its)]["discharge_time"].apply(np.datetime64)>(demo[demo["encounter_id"].astype(int).isin(Cefe_hadms_its)]["dod"].apply(np.datetime64)-np.timedelta64(90,'D')))/len(Cefe_hadms_its)

0.5025197984161267

In [84]:
antibiotic_string='Cefa'
antibiotic_id = [225850]
Cefa_hadms_its_only, Cefa_stay_list, Cefa_stay_times = u.patient_stay_search_antibiotic(antibiotic_string=antibiotic_string,antibiotic_id=antibiotic_id,prescriptions=abx2,icu_inputevents=abx3,icustays=icustays)

with open('D:/Mimic_data/Cefa_hadms_its_only.pkl', 'wb') as handle:
    pickle.dump(Cefa_hadms_its_only, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/Cefa_stay_list.pkl', 'wb') as handle:
    pickle.dump(Cefa_stay_list, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/Cefa_stay_times.pkl', 'wb') as handle:
    pickle.dump(Cefa_stay_times, handle, protocol=pickle.HIGHEST_PROTOCOL)

Number of Patients treated only with Cefazolin

In [16]:
with open('E:/Mimic_data/Cefa_hadms_its_only.pkl', 'rb') as handle:
    Cefa_hadms_its_only = pickle.load(handle)
    
len(Cefa_hadms_its_only)

2961

90-days mortality rate for Cefazolin

In [101]:
sum(demo[demo["encounter_id"].astype(int).isin(Cefa_hadms_its)]["discharge_time"].apply(np.datetime64)>(demo[demo["encounter_id"].astype(int).isin(Cefa_hadms_its)]["dod"].apply(np.datetime64)-np.timedelta64(90,'D')))/len(Cefa_hadms_its)

0.13803411288904519

In [ ]:
antibiotic_string='Piperacillin-Tazobactam|Vancomycin|CefTRI'
antibiotic_id = [225893,225798,225855]
three_hadms_its_only, three_stay_list, three_stay_times = u.patient_stay_search_antibiotic(antibiotic_string=antibiotic_string,antibiotic_id=antibiotic_id,prescriptions=abx2,icu_inputevents=abx3,icustays=icustays)

with open('D:/Mimic_data/three_hadms_its_only.pkl', 'wb') as handle:
    pickle.dump(three_hadms_its_only, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/three_stay_list.pkl', 'wb') as handle:
    pickle.dump(three_stay_list, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/three_stay_times.pkl', 'wb') as handle:
    pickle.dump(three_stay_times, handle, protocol=pickle.HIGHEST_PROTOCOL)

Number of Patients treated only with Piperacillin/Tazobactam, Vancomycin and Ceftriaxone

In [42]:
len(three_hadms_its_only)

3676

90-days mortality rate of Patients treated only with Piperacillin/Tazobactam, Vancomycin and Ceftriaxone

In [51]:
sum(demo[demo["encounter_id"].astype(int).isin(three_hadms_its)]["discharge_time"].apply(np.datetime64)>(demo[demo["encounter_id"].astype(int).isin(three_hadms_its)]["dod"].apply(np.datetime64)-np.timedelta64(90,'D')))/len(three_hadms_its)

0.3832875637504904

Microbiological data

In [29]:
from sqlalchemy import create_engine
# Postgres username, password, and database name
POSTGRES_ADDRESS = '127.0.0.1' ## INSERT YOUR DB ADDRESS
POSTGRES_PORT = '5432' ## INSERT YOUR PORT (DEFAULT IS 5432)
POSTGRES_USERNAME = 'wendland' ## INSERT YOUR POSTGRES USERNAME
POSTGRES_PASSWORD = '8c2oV00a' ## INSERT YOUR POSTGRES PASSWORD
POSTGRES_DBNAME = 'mimiciv'  ## INSERT YOUR POSTGRES DATABASE NAME


# A long string that contains the necessary Postgres login information
postgres_str = ('postgresql://{username}:{password}@{ipaddress}:{port}/{dbname}'.format(username=POSTGRES_USERNAME,password=POSTGRES_PASSWORD,ipaddress=POSTGRES_ADDRESS,port=POSTGRES_PORT,dbname=POSTGRES_DBNAME))

# Create the connection
cnx = create_engine(postgres_str)
def make_sorter(l):
    """
    Create a dict from the list to map to 0..len(l)
    Returns a mapper to map a series to this custom sort order
    """
    sort_order = {k:v for k,v in zip(l, range(len(l)))}
    return lambda s: s.map(lambda x: sort_order[x])
adt['encounter_id']=adt['encounter_id'].astype(int)
adt['patient_id']=adt['patient_id'].astype(int)
patient_id = adt[adt['encounter_id'].isin(three_hadms_its_only)].sort_values('encounter_id',key=make_sorter(three_hadms_its_only)).drop_duplicates('encounter_id')


microbiol = u.load_microbiologyevents(Patients=patient_id,cnx=cnx)
microbiol_all = u.load_microbiologyevents_all(Pateints=patient,cnx=cnx)


loading WITH mb AS (SELECT
    subject_id, hadm_id, charttime, spec_itemid, spec_type_desc, storetime,
test_itemid, test_name, org_itemid, org_name, ab_itemid, ab_name,
dilution_text, dilution_comparison, dilution_value, interpretation

    FROM mimiciv_hosp.microbiologyevents as all_mb
    WHERE interpretation = 'S' or interpretation='R' or interpretation='I' or interpretation='P')
    SELECT * FROM mb...

In [30]:
microbiol.groupby('spec_type_desc').count()['subject_id']

spec_type_desc
ABSCESS                                      900
ASPIRATE                                       7
BILE                                         449
BIOPSY                                         5
BLOOD CULTURE                               7751
BLOOD CULTURE ( MYCO/F LYTIC BOTTLE)           5
BRONCHIAL WASHINGS                           236
BRONCHOALVEOLAR LAVAGE                       660
CATHETER TIP-IV                              564
CORNEAL EYE SCRAPINGS                          9
CSF;SPINAL FLUID                              72
DIALYSIS FLUID                                40
EAR                                           35
FLUID RECEIVED IN BLOOD CULTURE BOTTLES      187
FLUID WOUND                                   17
FLUID,OTHER                                  182
FOOT CULTURE                                 103
FOREIGN BODY                                 201
Isolate                                       22
JOINT FLUID                                  197
MRSA 

In [31]:
pd.set_option('display.max_rows', 106)
print(microbiol.groupby('org_name').count()['subject_id'])

org_name
ABIOTROPHIA/GRANULICATELLA SPECIES                                           32
ACHROMOBACTER (ALCALIGENES) DENTRIFICANS                                     10
ACHROMOBACTER SP.                                                            26
ACINETOBACTER BAUMANNII                                                      88
ACINETOBACTER BAUMANNII COMPLEX                                             149
ACINETOBACTER LWOFFII                                                        11
ACINETOBACTER SP.                                                            10
ACTINOMYCES ODONTOLYTICUS                                                     2
ACTINOMYCES SP.                                                               2
AEROCOCCUS URINAE                                                             3
AEROMONAS HYDROPHILA COMPLEX                                                 11
ALCALIGENES SPECIES                                                          12
BACILLUS CEREUS/THURINGIENSIS  

In [25]:
with open('D:/Mimic_data/microbiol_three.pkl', 'wb') as handle:
    pickle.dump(microbiol, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [32]:
microbiol2 = microbiol[microbiol["spec_type_desc"].isin(["ABSCESS","BLOOD CULTURE","BRONCHIAL WASHINGS","BRONCHOALVEOLAR LAVAGE","SPUTUM","TISSUE","URINE"])]
microbiol3 = microbiol2[microbiol2["org_name"].isin(["ACINETOBACTER BAUMANNII","ACINETOBACTER BAUMANNII COMPLEX","BETA STREPTOCOCCUS GROUP A", "BETA STREPTOCOCCUS GROUP B","BETA STREPTOCOCCUS GROUP G","BURKHOLDERIA XENOVORANS", "CITROBACTER AMALONATICUS", "CITROBACTER FREUNDII COMPLEX", "CITROBACTER KOSERI", "CITROBACTER SPECIES", "CORYNEBACTERIUM SPECIES (DIPHTHEROIDS)", "ENTEROBACTER AEROGENES", "ENTEROBACTER CLOACAE", "ENTEROBACTER CLOACAE COMPLEX", "ENTEROBACTER SPECIES", "ENTEROBACTERIACEAE", "ENTEROCOCCUS FAECALIS", "ENTEROCOCCUS FAECIUM", "ENTEROCOCCUS SP.", "ESCHERICHIA COLI", "KLEBSIELLA OXYTOCA", "KLEBSIELLA PNEUMONIAE", "MORGANELLA MORGANII", "PASTEURELLA MULTOCIDA", "POSITIVE FOR METHICILLIN RESISTANT STAPH AUREUS", "PROTEUS MIRABILIS", "PSEUDOMONAS AERUGINOSA", "SALMONELLA SPECIES", "SERRATIA MARCESCENS", "STAPH AUREUS COAG +", "STAPHYLOCOCCUS CAPITIS", "STAPHYLOCOCCUS EPIDERMIDIS", "STAPHYLOCOCCUS HAEMOLYTICUS", "STAPHYLOCOCCUS HOMINIS", "STAPHYLOCOCCUS LUGDUNENSIS", "STAPHYLOCOCCUS, COAGULASE NEGATIVE", "STENOTROPHOMONAS MALTOPHILIA", "STREPTOCOCCUS ANGINOSUS", "STREPTOCOCCUS ANGINOSUS (MILLERI) GROUP", "STREPTOCOCCUS BOVIS ", "STREPTOCOCCUS BOVIS GROUP", "STREPTOCOCCUS GALLOLYTICUS SSP. PASTEURIANUS (STREPTOCOCCUS BOVIS)", "STREPTOCOCCUS PNEUMONIAE", "STREPTOCOCCUS SALIVARIUS", "VIRIDANS STREPTOCOCCI"])]
microbiol4 = microbiol3[microbiol3["ab_name"].isin(['CEFTRIAXONE','PIPERACILLIN/TAZO','VANCOMYCIN','PIPERACILLIN'])]

In [ ]:
#microbiol2_all = microbiol_all[microbiol_all["spec_type_desc"].isin(["ABSCESS","BLOOD CULTURE","BRONCHIAL WASHINGS","BRONCHOALVEOLAR LAVAGE","SPUTUM","TISSUE","URINE"])]microbiol3 = microbiol2[microbiol2["org_name"].isin(["ACINETOBACTER BAUMANNII","ACINETOBACTER BAUMANNII COMPLEX","BETA STREPTOCOCCUS GROUP A", "BETA STREPTOCOCCUS GROUP B","BETA STREPTOCOCCUS GROUP G","BURKHOLDERIA XENOVORANS", "CITROBACTER AMALONATICUS", "CITROBACTER FREUNDII COMPLEX", "CITROBACTER KOSERI", "CITROBACTER SPECIES", "CORYNEBACTERIUM SPECIES (DIPHTHEROIDS)", "ENTEROBACTER AEROGENES", "ENTEROBACTER CLOACAE", "ENTEROBACTER CLOACAE COMPLEX", "ENTEROBACTER SPECIES", "ENTEROBACTERIACEAE", "ENTEROCOCCUS FAECALIS", "ENTEROCOCCUS FAECIUM", "ENTEROCOCCUS SP.", "ESCHERICHIA COLI", "KLEBSIELLA OXYTOCA", "KLEBSIELLA PNEUMONIAE", "MORGANELLA MORGANII", "PASTEURELLA MULTOCIDA", "POSITIVE FOR METHICILLIN RESISTANT STAPH AUREUS", "PROTEUS MIRABILIS", "PSEUDOMONAS AERUGINOSA", "SALMONELLA SPECIES", "SERRATIA MARCESCENS", "STAPH AUREUS COAG +", "STAPHYLOCOCCUS CAPITIS", "STAPHYLOCOCCUS EPIDERMIDIS", "STAPHYLOCOCCUS HAEMOLYTICUS", "STAPHYLOCOCCUS HOMINIS", "STAPHYLOCOCCUS LUGDUNENSIS", "STAPHYLOCOCCUS, COAGULASE NEGATIVE", "STENOTROPHOMONAS MALTOPHILIA", "STREPTOCOCCUS ANGINOSUS", "STREPTOCOCCUS ANGINOSUS (MILLERI) GROUP", "STREPTOCOCCUS BOVIS ", "STREPTOCOCCUS BOVIS GROUP", "STREPTOCOCCUS GALLOLYTICUS SSP. PASTEURIANUS (STREPTOCOCCUS BOVIS)", "STREPTOCOCCUS PNEUMONIAE", "STREPTOCOCCUS SALIVARIUS", "VIRIDANS STREPTOCOCCI"])]
microbiol2_all = microbiol_all[microbiol_all["spec_type_desc"].isin(["BLOOD CULTURE"])]
fungus_virus_list=['ASPERGILLUS FUMIGATUS', 'ASPERGILLUS FUMIGATUS COMPLEX', 'ASPERGILLUS NIGER', 'ASPERGILLUS SP. NOT FUMIGATUS, FLAVUS OR NIGER', 'ASPERGILLUS SPECIES', 'CANDIDA ALBICANS', 'CANDIDA ALBICANS, PRESUMPTIVE IDENTIFICATION', 'CANDIDA DUBLINIENSIS', 'CANDIDA GLABRATA', 'CANDIDA GUILLIERMONDII', 'CANDIDA KEFYR', 'CANDIDA KRUSEI', 'CANDIDA LUSITANIAE', 'CANDIDA PARAPSILOSIS', 'CANDIDA SPECIES', 'CANDIDA TROPICALIS', 'CAPNOCYTOPHAGA SPECIES', 'HERPES SIMPLEX VIRUS TYPE 1', 'MOLD', 'MUCOR SP.', 'POSITIVE FOR CYTOMEGALOVIRUS', 'POSITIVE FOR INFLUENZA A VIRAL ANTIGEN', 'ROTHIA SPECIES', 'YEAST', 'YEAST, PRESUMPTIVELY NOT C. ALBICANS']
microbiol3_all = microbiol2_all[microbiol2_all["org_name"].isin(myco_virus_list)]
with open('D:/Mimic_data/microbiol_fungal_three.pkl', 'wb') as handle:
    pickle.dump(microbiol3_all handle, protocol=pickle.HIGHEST_PROTOCOL)


In [32]:
with open('D:/Mimic_data/microbiol_sel_three.pkl', 'wb') as handle:
    pickle.dump(microbiol4, handle, protocol=pickle.HIGHEST_PROTOCOL)

Selecting for the final three Antibiotic and the final patients all antibiotic data

In [45]:
icu_inputevents=abx3
antibiotic_id = [225893,225798,225855]
icu_inputevents[(icu_inputevents["hadm_id"]==20017989) & (~icu_inputevents["itemid"].isin(antibiotic_id))  & (icu_inputevents["ordercomponenttypedescription"] == "Main order parameter")]        

subject_id   hadm_id   stay_id  caregiver_id           starttime             endtime           storetime  itemid  amount amountuom  rate rateuom  orderid  linkorderid    ordercategoryname secondaryordercategoryname ordercomponenttypedescription ordercategorydescription  patientweight  totalamount totalamountuom  isopenbag  continueinnextdept statusdescription  originalamount  originalrate
519881    11044946  20017989  38167058          5073 2125-08-11 13:05:00 2125-08-11 13:06:00 2125-08-11 13:05:00  225879     1.0      dose   NaN    None  8975976      8975976  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push          104.2        100.0             ml          0                   0   FinishedRunning             1.0           1.0
519882    11044946  20017989  38167058          5073 2125-08-11 13:05:00 2125-08-11 13:06:00 2125-08-11 13:05:00  225892     1.0      dose   NaN    None  3242642      3242642  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push          104.2        100.0             ml          0                   0   FinishedRunning             1.0           1.0
519890    11044946  20017989  38167058          9847 2125-08-11 20:30:00 2125-08-11 20:31:00 2125-08-11 20:41:00  225892     1.0      dose   NaN    None  6837466      6837466  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push          104.2        100.0             ml          0                   0   FinishedRunning             1.0           1.0
519898    11044946  20017989  38167058          9847 2125-08-12 03:48:00 2125-08-12 03:49:00 2125-08-12 03:48:00  225892     1.0      dose   NaN    None  7617536      7617536  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push          104.2        100.0             ml          0                   0   FinishedRunning             1.0           1.0
519904    11044946  20017989  38167058          9847 2125-08-12 20:05:00 2125-08-12 20:06:00 2125-08-12 22:05:00  225890     1.0      dose   NaN    None  7697856      7697856  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push          104.2         50.0             ml          0                   0   FinishedRunning             1.0           1.0
519909    11044946  20017989  38167058          9847 2125-08-13 00:08:00 2125-08-13 00:09:00 2125-08-13 05:08:00  225890     1.0      dose   NaN    None  2062232      2062232  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push          104.2         50.0             ml          0                   0   FinishedRunning             1.0           1.0
519914    11044946  20017989  38167058          9847 2125-08-13 04:09:00 2125-08-13 04:10:00 2125-08-13 05:09:00  225890     1.0      dose   NaN    None  6916672      6916672  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push          104.2         50.0             ml          0                   0   FinishedRunning             1.0           1.0
519937    11044946  20017989  38167058         72035 2125-08-12 16:45:00 2125-08-12 16:46:00 2125-08-12 17:03:00  225890     1.0      dose   NaN    None  7138702      7138702  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push          104.2         50.0             ml          0                   0   FinishedRunning             1.0           1.0
519940    11044946  20017989  38167058         72035 2125-08-13 07:45:00 2125-08-13 07:46:00 2125-08-13 07:52:00  225890     1.0      dose   NaN    None  1097570      1097570  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push          104.2         50.0             ml          0                   0   FinishedRunning             1.0           1.0

In [ ]:
three_antibiotics=u.get_antibiotic_administrations(three_stay_list,antibiotic_id=[225893,225798,225855],antibiotic_string='Piperacillin-Tazobactam|Vancomycin|CefTRI',prescriptions=abx2,icu_inputevents=abx3)

with open('D:/Mimic_data/three_antibiotics.pkl', 'wb') as handle:
    pickle.dump(three_antibiotics, handle, protocol=pickle.HIGHEST_PROTOCOL)


In [16]:
three_antibiotics

subject_id   hadm_id   stay_id  caregiver_id           starttime             endtime           storetime  itemid  amount amountuom  rate rateuom  orderid  linkorderid    ordercategoryname secondaryordercategoryname ordercomponenttypedescription ordercategorydescription  patientweight  totalamount totalamountuom  isopenbag  continueinnextdept statusdescription  originalamount  originalrate
1906393    13726263  26173973  38304144         61883 2142-12-25 04:14:00 2142-12-25 04:15:00 2142-12-25 04:15:00  225893    2.25         g   NaN    None  4912789      4912789  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push          113.5         50.0             ml          0                   0   FinishedRunning             1.0           1.0
1906413    13726263  26173973  38304144         98952 2142-12-25 12:37:00 2142-12-25 12:38:00 2142-12-25 12:37:00  225893    2.25         g   NaN    None  6388231      6388231  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push          113.5         50.0             ml          0                   0   FinishedRunning             1.0           1.0
1909242    13731023  26420563  35063248         24745 2132-02-13 23:30:00 2132-02-13 23:31:00 2132-02-13 23:30:00  225893    4.50         g   NaN    None  3100579      3100579  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push           84.6        100.0             ml          0                   0   FinishedRunning             1.0           1.0
1909257    13731023  26420563  35063248         62920 2132-02-14 08:00:00 2132-02-14 08:01:00 2132-02-14 09:29:00  225893    2.25         g   NaN    None  5859357      5859357  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push           84.6        100.0             ml          0                   0   FinishedRunning             1.0           1.0
1846319    13614165  21964447  33738212         26395 2170-09-02 03:11:00 2170-09-02 03:12:00 2170-09-02 03:42:00  225893    4.50         g   NaN    None  8693720      8693720  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push           70.5        100.0             ml          0                   0   FinishedRunning             1.0           1.0
...             ...       ...       ...           ...                 ...                 ...                 ...     ...     ...       ...   ...     ...      ...          ...                  ...                        ...                           ...                      ...            ...          ...            ...        ...                 ...               ...             ...           ...
4075452    17793986  27884767  30578595         62411 2130-07-16 12:00:00 2130-07-16 12:01:00 2130-07-16 13:52:00  225893    2.25         g   NaN    None  3784153      3784153  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push           55.0         50.0             ml          0                   0   FinishedRunning             1.0           1.0
4075455    17793986  27884767  30578595         83370 2130-07-15 20:17:00 2130-07-15 20:18:00 2130-07-15 20:17:00  225893    2.25         g   NaN    None  3651783      3651783  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push           55.0        100.0             ml          0                   0   FinishedRunning             1.0           1.0
4075458    17793986  27884767  30578595         83370 2130-07-16 04:24:00 2130-07-16 04:25:00 2130-07-16 04:24:00  225893    2.25         g   NaN    None  1389213      1389213  08-Antibiotics (IV)   02-Fluids (Crystalloids)          Main order parameter                Drug Push           55.0         50.0             ml          0                   0   FinishedRunning             1.0           1.0

In [166]:
three_antibiotics_prescriptions=abx2[(abx2["hadm_id"].isin(three_hadms_its_only)) & (abx2["antibiotic"].str.contains(antibiotic_string)) & (abx2["route"].astype(str)=="IV")]

with open('D:/Mimic_data/three_antibiotics_prescriptions.pkl', 'wb') as handle:
    pickle.dump(three_antibiotics_prescriptions, handle, protocol=pickle.HIGHEST_PROTOCOL)

### Variable selection

In [ ]:
python_SOFA2=python_SOFA.copy()
python_SOFA2["label"]="SOFA"
python_SOFA2["score_time"]=python_SOFA2["score_time"].dt.tz_localize(None)
python_SOFA2=python_SOFA2.rename({'encounter_id': 'hadm_id', 'score_time': 'time_measured', 'SOFA_Score': 'value'}, axis='columns')
python_SOFA2=python_SOFA2[python_SOFA2["hadm_id"].isin(Sep_3["encounter_id"])]
python_SOFA2["storetime"]=python_SOFA2["time_measured"]

lab_comp=lab_comp.append(python_SOFA2[["patient_id","time_measured","storetime","value","label","hadm_id"]])

lab_comp["hadm_id"]=lab_comp["hadm_id"].astype(int)
Sep_3["encounter_id"]=Sep_3["encounter_id"].astype(int)
icustays["hadm_id"]=icustays["hadm_id"].astype(int)

#Variables rounded to 12 hours for correlation
mean_lab_patients_12h_oneweek_icu,mean_lab_patients_12h_variables_icu= u.multiple_patients_mean(lab_comp, hadm_ids=lab_comp["hadm_id"].unique(), round_nearest=True, round_minutes=60*12, aggregate_startvalues=True, remove_unaggregated_values=True, max_time=168, start_hours=6, start_timepoint='sepsis_icu', sep_data=Sep_3, lab_demo=lab_demo3, just_icu=True, icustays=icustays)

#Variables rounded to 1 hour for missing value determination and creating training data
mean_lab_patients_1h_oneweek_icu,mean_lab_patients_1h_variables_icu= u.multiple_patients_mean(lab_comp, hadm_ids=lab_comp["hadm_id"].unique(), round_nearest=True, round_minutes=60, aggregate_startvalues=True, remove_unaggregated_values=True, max_time=168, start_hours=0.5, start_timepoint='sepsis_icu', sep_data=Sep_3, lab_demo=lab_demo3, just_icu=True, icustays=icustays)

mean_1_sepsis = mean_lab_patients_1h_oneweek_icu

with open('D:/Mimic_data/mean_lab_patients_12h_oneweek_icu.pkl', 'wb') as handle:
    pickle.dump(mean_lab_patients_12h_oneweek_icu, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/mean_lab_patients_12h_variables_icu.pkl', 'wb') as handle:
    pickle.dump(mean_lab_patients_12h_variables_icu, handle, protocol=pickle.HIGHEST_PROTOCOL)
    
with open('D:/Mimic_data/mean_lab_patients_1h_oneweek_icu.pkl', 'wb') as handle:
    pickle.dump(mean_lab_patients_1h_oneweek_icu, handle, protocol=pickle.HIGHEST_PROTOCOL)
with open('D:/Mimic_data/mean_lab_patients_1h_variables_icu.pkl', 'wb') as handle:
    pickle.dump(mean_lab_patients_1h_variables_icu, handle, protocol=pickle.HIGHEST_PROTOCOL)

Removing all variables, where the median number of measurements for every patient is lower than 4

In [8]:
mean_1_sepsis.shape

torch.Size([26111, 169, 70])

In [12]:
torch.median(torch.sum(~mean_1_sepsis.isnan(),axis=1),axis=0)[0]

tensor([169,  56,   1,   0,   1,   1,   4,   1,   2,   0,   0,   4,   1,   4,
          4,   5,   4,  52,   0,   0,   1,  13,  13,  13,  13,  13,  12,  54,
          5,   4,   2,   1,   1,   0,   0,   0,   4,  52,   4,   4,   4,   0,
          0,   0,   0,   1,   2,   2,   4,   2,   5,   2,   2,   4,   4,  53,
         52,   5,  53,  17,   2,  22,  15,  26,  31,  31,  31,  31,   4,   1])

In [13]:
variables=variables_sepsis.insert(0,"time")

In [14]:
variables

Index(['time', 'SOFA', 'aado2_calc', 'albumin', 'alp', 'alt', 'aniongap', 'ast', 'baseexcess', 'basophils', 'basophils_abs', 'bicarbonate', 'bilirubin_total', 'bun', 'calcium', 'chloride', 'creatinine', 'dbp', 'eosinophils', 'eosinophils_abs', 'fio2', 'gcs', 'gcs_eyes', 'gcs_motor', 'gcs_unable', 'gcs_verbal', 'glucose', 'heart_rate', 'hematocrit', 'hemoglobin', 'inr', 'ionized calcium', 'lactate', 'ld_ldh', 'lymphocytes', 'lymphocytes_abs', 'magnesium', 'mbp', 'mch', 'mchc', 'mcv', 'monocytes', 'monocytes_abs', 'neutrophils', 'neutrophils_abs', 'pao2fio2ratio', 'pco2', 'ph', 'platelet', 'po2', 'potassium', 'pt', 'ptt', 'rbc', 'rdw', 'resp_rate', 'sbp', 'sodium', 'spo2', 'temperature', 'totalco2', 'uo_rt_12hr_kdigouo', 'uo_rt_24hr_kdigouo', 'uo_rt_6hr_kdigouo', 'urineoutput_12hr_kdigouo', 'urineoutput_24hr_kdigouo', 'urineoutput_6hr_kdigouo', 'urineoutput_kdigouo', 'wbc', 'weight'], dtype='object', name='label')

In [15]:
allowed_variables_ind=np.array(torch.median(torch.sum(~mean_1_sepsis.isnan(),axis=1),axis=0)[0]>=4,dtype=bool)

In [16]:
allowed_variables_sel=list(variables[np.array(torch.median(torch.sum(~mean_1_sepsis.isnan(),axis=1),axis=0)[0]>=4,dtype=bool)])
#removing redundant variables and adding bilirubin total
allowed_variables_sel = [e for e in allowed_variables_sel if e not in ["gcs","gcs_eyes","gcs_unable","gcs_motor","gcs_verbal","uo_rt_12hr_kdigouo","uo_rt_24hr_kdigouo","urineoutput_12hr_kdigouo","urineoutput_24hr_kdigouo","urineoutput_kdigouo"]] + ["bilirubin_total"]
allowed_variables_sel

['time',
 'SOFA',
 'aniongap',
 'bicarbonate',
 'bun',
 'calcium',
 'chloride',
 'creatinine',
 'dbp',
 'glucose',
 'heart_rate',
 'hematocrit',
 'hemoglobin',
 'magnesium',
 'mbp',
 'mch',
 'mchc',
 'mcv',
 'platelet',
 'potassium',
 'rbc',
 'rdw',
 'resp_rate',
 'sbp',
 'sodium',
 'spo2',
 'temperature',
 'uo_rt_6hr_kdigouo',
 'urineoutput_6hr_kdigouo',
 'wbc',
 'bilirubin_total']

In [17]:
len(allowed_variables_sel)

31

In [76]:
with open('D:/Mimic_data/allowed_variables_sel_sepsis.pkl', 'wb') as handle:
    pickle.dump(allowed_variables_sel, handle, protocol=pickle.HIGHEST_PROTOCOL)

Computing tensors of the spearman correlation

In [ ]:
mean_12_sepsis = mean_lab_patients_12h_oneweek_icu
mean_12_sepsis=mean_12_sepsis[:,:-1,:]

corr_tensor=torch.empty(size=mean_12_sepsis.shape[1:])
from torchmetrics import SpearmanCorrCoef
spearman = SpearmanCorrCoef()

mean_lab_patients_12h_variables_icu=list(mean_lab_patients_12h_variables_icu)
mean_lab_patients_12h_variables_icu.insert(0,"Time")
SOFA_index=mean_lab_patients_12h_variables_icu.index("SOFA")
SOFA_sepsis_mean=mean_12_sepsis[:,:,SOFA_index]

for i in range(mean_12_sepsis.shape[1]):
    for j in range(mean_12_sepsis.shape[2]):
        corr_tensor[i,j] = pd.DataFrame(SOFA_sepsis_mean[:,i]).corrwith(pd.DataFrame(mean_12_sepsis[:,i,j]),method='spearman')[0]
            
with open('D:/Mimic_data/corr_tensor_sepsis_12h.pkl', 'wb') as handle:
    pickle.dump(corr_tensor, handle, protocol=pickle.HIGHEST_PROTOCOL)
    


Plots of the correlation and nan values

In [ ]:
for i in range(len(mean_lab_patients_12h_variables_icu)):
    plt.figure()
    lo = plt.scatter(np.arange(corr_tensor.shape[0]), corr_tensor[:,i], marker='o')#, color=colors[0])
    
    plt.title("Sepsis Patients Spearman Correlation " + mean_lab_patients_12h_variables_icu[i])
    plt.xlabel("Time in hours")
    plt.ylabel("Spearman Correlation")
    plt.xlim([0, corr_tensor.shape[0]])
    plt.ylim([-1, 1])
    
    plt.savefig('sepsis_12h_spearman_' + mean_lab_patients_12h_variables_icu[i]+ '.jpg',bbox_inches='tight')
    
for i in range(len(mean_lab_patients_12h_variables_icu)):
    plt.figure()
    lo = plt.scatter(np.arange(mean_12_sepsis.shape[1]), torch.sum(mean_12_sepsis[:,:,i].isnan(),axis=0)/mean_12_sepsis[:,:,i].shape[0], marker='o')
    plt.title("Sepsis Patients Na percentage of " + mean_lab_patients_12h_variables_icu[i])
    plt.xlabel("Time in hours")
    plt.ylabel("Value")
    plt.xlim([0, mean_12_sepsis.shape[1]])
    plt.ylim([0, 1])
    
    plt.savefig('sepsis_12h_na_' + mean_lab_patients_12h_variables_icu[i]+ '.jpg',bbox_inches='tight')



In [35]:
[e for e in list(variables[(torch.abs(corr_tensor_sepsis_12h)>0.3).any(dim=0).numpy() & (variables_ind)]) if e not in rl]

['SOFA',
 'aniongap',
 'bicarbonate',
 'bun',
 'creatinine',
 'dbp',
 'mbp',
 'platelet',
 'rdw',
 'sbp']

### Creating tensors for OptAB

Determining SOFA-Score for shorter time periods of the final patients (here 15 minutes)

In [ ]:
import pickle
import utils as u
sql_scripts=u.sql_queries_start()
    
from sqlalchemy import create_engine
# Postgres username, password, and database name
POSTGRES_ADDRESS = '127.0.0.1' ## INSERT YOUR DB ADDRESS
POSTGRES_PORT = '5432' ## INSERT YOUR PORT (DEFAULT IS 5432)
POSTGRES_USERNAME = 'wendland' ## INSERT YOUR POSTGRES USERNAME
POSTGRES_PASSWORD = '8c2oV00a' ## INSERT YOUR POSTGRES PASSWORD
POSTGRES_DBNAME = 'mimiciv'  ## INSERT YOUR POSTGRES DATABASE NAME


# A long string that contains the necessary Postgres login information
postgres_str = ('postgresql://{username}:{password}@{ipaddress}:{port}/{dbname}'.format(username=POSTGRES_USERNAME,password=POSTGRES_PASSWORD,ipaddress=POSTGRES_ADDRESS,port=POSTGRES_PORT,dbname=POSTGRES_DBNAME))

# Create the connection
cnx = create_engine(postgres_str)
data = u.load_dfs(sql_scripts,cnx,patients=three_hadms_its_only)

#FINALIZE DATAFRAMES
lvdf = data['lvdf'].copy()
adt = u.make_adt(data['adt'],data['icu_adt'])
vasodf = data['vasodf'].copy()
dxdf = data['dxdf'].copy()
mvdf = data['mvdf'].copy()
abxdf = data['abxdf'].copy()
cxdf = data['cxdf'].copy()
demo = data['demo'].copy()
Sepsis3_key = data['Sepsis3'].copy()
uo = data['uo'].copy()

names_to_standard = {
            'subject_id' : 'patient_id', 
            'hadm_id' : 'encounter_id', 
            'admittime' : 'admit_time', 
            'dischtime' : 'discharge_time',
            'adt_loc': 'location',
            'intime_hr': 'location_start',
            'outtime_hr':'location_end',
        
            
            
            'val' : 'value', 
            'mark' : 'label', 
            'time' : 'time_measured', 
            
            
            'vent_start': 'vent_start',
            'vent_end':'vent_end',
            'ventilation_status': 'vent_type',
            
            
            'vaso_start': 'vaso_start',
            'vaso_end': 'vaso_end',
            'rate_uom': 'vaso_units',
            'rate': 'vaso_dose',
            'drug': 'pressor_name',
            

            'starttime':'abx_start',
            'stoptime': 'abx_end',
            'antibiotic' : 'antibiotic_name',
            
            
            'charttime': 'culture_time',
            'spec_type_desc': 'culture_type',
    
            'icd_code' : 'dx_code',
            'recorded_date' : 'dx_time',
    
            'uo_time':'uo_time'
       }
dfs=[lvdf, adt, vasodf, dxdf, mvdf, abxdf, cxdf, demo , Sepsis3_key , uo]
for df in dfs:
    df.rename(columns=names_to_standard,inplace=True)
    display(df.head())
# DROP COLUMNS THAT ARE NOT NEEDED
adt = adt.drop(columns=['admit_time','discharge_time'])
vasodf = vasodf.drop(columns=['encounter_id'])
lvdf = lvdf.drop(columns=['encounter_id'])
mvdf = mvdf.drop(columns=['stay_id'])
abxdf = abxdf.drop(columns=['encounter_id','stay_id'])
cxdf = cxdf.drop(columns=['encounter_id','micro_specimen_id','chartdate','positiveculture'])
uo = uo.drop(columns=['encounter_id'])
mvdf = mvdf[mvdf['vent_type'].isin(['InvasiveVent'])].reset_index(drop=True)
mvdf.loc[mvdf['vent_type']=='InvasiveVent','vent_type']='VENT'
vasodf = vasodf[vasodf['pressor_name'].isin(['norepinephrine','epinephrine','dopamine','dobutamine'])].reset_index(drop=True)
lvdf_map = {#'TEMP' : 'temp_c', 
            'HR' : 'hr', 
            'RR' :  'rr',
            #'PCO2': 'pco2_art',
            'WBC' : 'wbc',
            'SBP' : 'sbp',
            'MAP' : 'map',
            #'LACTATE' : 'lactate',
            'Cr' : 'cr',
            'BILI' : 'bili',
            'PLT' : 'plt',
            #'INR' : 'inr',
            #'PT' : 'pt',
            'GCS' : 'gcs',
            'FiO2': 'fio2',
            'O2_Flow': 'O2 Flow',
            'SpO2' : 'spo2',
            'BUN' : 'bun',
            #'PT' : 'pt',
            #'UOP' : np.nan,
            'FiO2' : 'fio2',
            #'pH' : 'ph_art',
            'pO2' : 'pO2',
            #'AaGradient' : np.nan,
            #'Na': 'na',
            #'K' : 'k',
            #'HCT' : 'hcrt',
            #'PTT': 'ptt',
            #'PEEP': 'peep',
            #'PFRatio': np.nan,
            #'SFRatio': np.nan,
           }

inv_map = {v: k for k, v in lvdf_map.items() if pd.notna(k)}

lvdf['label']  = lvdf['label'].map(inv_map)
lvdf['time_measured'] = pd.to_datetime(lvdf['time_measured'],utc=True)
lvdf.drop_duplicates(inplace= True)

lvdf = lvdf[~lvdf['value'].isna()]

cx_final=cxdf
SOI_full, RTI_full, Sep_3,SOI_final,RTI_final = I2_Sepsis.Sepsis_3(lvdf=lvdf, adt=adt, mvdf= mvdf, abxdf = abxdf, cxdf= cx_final, vasodf = vasodf, uodf=uo, demo=demo, SF_dict = {1:512,2:357,3:214,4:89}, calc_FiO2 = False, calc_PF = True, calc_SF= False, 
max_flow_convert= 6, calc_interval_mins = 15, LOCF_hours = None, include_SF_RATIO = False, include_qSOFA =False,mech_vent_def = 'VENT', gcs_cutoff = 15, debug = True, cutoff = 2)
Sep_3_orig,RTI_orig,SOI_orig,MSep_3,MIMIC_SOI,MIMIC_SOFA,Sep_3,RTI,python_SOFA,SOI_trim=u.cleanup_sep3(Sep_3,RTI_full,SOI_full,data,names_to_standard,cnx)

SOFA_three_15 = python_SOFA

Format processing steps

In [60]:
three_antibiotics_prescriptions2=three_antibiotics_prescriptions.copy()
three_antibiotics_prescriptions2.loc[three_antibiotics_prescriptions2["antibiotic"]=="CefTRIAXone","antibiotic"]="Ceftriaxon"
three_antibiotics_prescriptions2=three_antibiotics_prescriptions2.rename({'antibiotic': 'label'}, axis='columns')
three_antibiotics_prescriptions2.loc[three_antibiotics_prescriptions2["stay_id"].notna(),"stay_id"] = three_antibiotics_prescriptions2.loc[three_antibiotics_prescriptions2["stay_id"].notna(),"stay_id"].astype(int)
three_antibiotics_prescriptions2["hadm_id"]=three_antibiotics_prescriptions2["hadm_id"].astype(int)
three_antibiotics_prescriptions2["patient_id"]=three_antibiotics_prescriptions2["patient_id"].astype(int)

three_antibiotics2=three_antibiotics.copy()
three_antibiotics2["label"]=''
three_antibiotics2.loc[three_antibiotics2["itemid"]==225798,"label"]='Vancomycin'
three_antibiotics2.loc[three_antibiotics2["itemid"]==225893,"label"]='Piperacillin-Tazobactam'
three_antibiotics2.loc[three_antibiotics2["itemid"]==225855,"label"]='Ceftriaxon'
three_antibiotics2=three_antibiotics2.rename({'subject_id': 'patient_id', 'starttime': 'time_measured', 'amount': 'value'}, axis='columns')
three_antibiotics2["stay_id"]=three_antibiotics2["stay_id"].astype(int)
three_antibiotics2["hadm_id"]=three_antibiotics2["hadm_id"].astype(int)
three_antibiotics2["patient_id"]=three_antibiotics2["patient_id"].astype(int)
three_antibiotics2["value"]=three_antibiotics2["value"].astype(float)

SOFA_three_15_2=SOFA_three_15.copy()
SOFA_three_15_2["label"]="SOFA"
SOFA_three_15_2["encounter_id"]=SOFA_three_15_2["encounter_id"].astype(int)
SOFA_three_15_2["patient_id"]=SOFA_three_15_2["patient_id"].astype(int)
SOFA_three_15_2["score_time"]=SOFA_three_15_2["score_time"].dt.tz_localize(None)
SOFA_three_15_2=SOFA_three_15_2.rename({'encounter_id': 'hadm_id', 'score_time': 'time_measured', 'SOFA_Score': 'value'}, axis='columns')
SOFA_three_15_2=SOFA_three_15_2[SOFA_three_15_2["hadm_id"].isin(Sep_3["encounter_id"].astype(int))]
SOFA_three_15_2["storetime"]=SOFA_three_15_2["time_measured"]

lab_comp["hadm_id"]=lab_comp["hadm_id"].astype(int)
lab_comp=lab_comp.append(SOFA_three_15_2[["patient_id","time_measured","storetime","value","label","hadm_id"]])

variables_enough=['SOFA','aniongap','bicarbonate','bun','creatinine','dbp','platelet','rdw','sbp','bilirubin_total','alt']
lab_comp=lab_comp[lab_comp["label"].isin(variables_enough)]
lab_comp=lab_comp[lab_comp["hadm_id"].isin(three_hadms_its_only)]
antibiotics_variables=["Vancomycin","Piperacillin-Tazobactam","Ceftriaxon"]
three_antibiotics_prescriptions2=three_antibiotics_prescriptions2[three_antibiotics_prescriptions2["label"].isin(antibiotics_variables)]


C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\4200255925.py:29: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  lab_comp=lab_comp.append(SOFA_three_15_2[["patient_id","time_measured","storetime","value","label","hadm_id"]])


Creating tensor, which can be used by OptAB

In [ ]:
tensor, key_dict, variables_tensor, variables_complete, complete_stay_list, static_tensor, static_variables, fit, variables_mean, variables_std, static_mean, static_std, indices_train, indices_test=u.multiple_patients_predictions_tensor(min_pred=0,max_pred=None, pred_times_in_h=1,lab_df=lab_comp,thresh=None, sep_data=Sep_3, round_time=False, round_nearest=True, round_minutes=60, aggregate_startvalues=True, start_hours=1, remove_unaggregated_values=True, start_timepoint='sepsis_icu', lab_demo=lab_demo3,print_=True,list_of_hadms=None,just_icu=True,icustays=icustays,stays_list=three_stay_list,variables=variables_enough, missing_imputation_start=True, antibiotics=three_antibiotics_prescriptions2,remove_noant=True, static=static, static_time=False, standardize=True, train_test_split=True, seed=0,antibiotics_variables=antibiotics_variables,binary_antibiotics=True,static_bin_ant=True)
# tensor: Tensor containing all dynamic variables (including time on the first channel, antibiotics, and missing masks) for OptAB, size: batch x timepoints x variables
# key_dict: Dictionary mapping time index to time in hours (here 1 index = 1 hour, therefore not necessary)
# variables_tensor: List containing all labels of the dynamic variables, which are standardized (variables, without time and missing masks)
# variables_complete: List containing all labels of the dynamic variables
# complete_stay_list: List of stay indices for the patients
# static_tensor: Tensor containing all static variables for OptAB, size: batch x variables
# static_variables: List containing all labels of the static variables
# fit: Fitted knn_imputer object 
# variables_mean and variables_std: Lists containing all means and standard deviations used for standardization of the dynamic variables
# static_mean and static_std: Lists containing all means and standard deviations used for standardization of the static variables
# indices_train and indices_test: Lists containing the training and test indices of the data

with open('D:/Mimic_data/sepsis_all_1_lab.pkl', 'wb') as handle:
    pickle.dump(tensor, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/sepsis_all_1_keys.pkl', 'wb') as handle:
    pickle.dump(key_dict, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/sepsis_all_1_variables.pkl', 'wb') as handle:
    pickle.dump(variables_tensor, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/sepsis_all_1_variables_complete.pkl', 'wb') as handle:
    pickle.dump(variables_complete, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/sepsis_all_1_complete_stays.pkl', 'wb') as handle:
    pickle.dump(complete_stay_list, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/sepsis_all_1_static.pkl', 'wb') as handle:
    pickle.dump(static_tensor, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/sepsis_all_1_static_variables.pkl', 'wb') as handle:
    pickle.dump(static_variables, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/sepsis_all_1_imputer.pkl', 'wb') as handle:
    pickle.dump(fit, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/sepsis_all_1_variables_mean.pkl', 'wb') as handle:
    pickle.dump(variables_mean, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/sepsis_all_1_variables_std.pkl', 'wb') as handle:
    pickle.dump(variables_std, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/sepsis_all_1_static_mean.pkl', 'wb') as handle:
    pickle.dump(static_mean, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/sepsis_all_1_static_std.pkl', 'wb') as handle:
    pickle.dump(static_std, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/sepsis_all_1_indices_train.pkl', 'wb') as handle:
    pickle.dump(indices_train, handle, protocol=pickle.HIGHEST_PROTOCOL)

with open('D:/Mimic_data/sepsis_all_1_indices_test.pkl', 'wb') as handle:
    pickle.dump(indices_test, handle, protocol=pickle.HIGHEST_PROTOCOL)




In [78]:
creat_dat = u.multiple_patients_creatinine_preproc(lab_comp, start_hours=1, timetype="time_measured", start_timepoint='sepsis_icu', sep_data=Sep_3, lab_demo=lab_demo3,just_icu=True, icustays=icustays, stays_list=complete_stay_list)
#list of dataframes of creatinine values for all considered patients
#Necessary for computation of Acute Kidney injury for optimal treatment selection (as side-effect)

with open('D:/Mimic_data/creat_dat.pkl', 'wb') as handle:
    pickle.dump(creat_dat, handle, protocol=pickle.HIGHEST_PROTOCOL)

In [82]:
microbiol_dat = u.multiple_patients_microbiol_preproc(microbiol4, lab_comp, start_hours=1, timetype="time_measured", start_timepoint='sepsis_icu', sep_data=Sep_3, lab_demo=lab_demo3,just_icu=True, icustays=icustays, stays_list=complete_stay_list)

#list of dataframes of microbiologica data for all considered patients
#Necessary for optimal treatment selection

with open('D:/Mimic_data/microbiol_dat_.pkl', 'wb') as handle:
    pickle.dump(microbiol_dat, handle, protocol=pickle.HIGHEST_PROTOCOL)

microbiol3_all['chartdate'] = microbiol3_all['charttime']
microbiol_fungal_dat = u.multiple_patients_microbiol_preproc(microbiol3_all, lab_comp, start_hours=1, timetype="time_measured", start_timepoint='sepsis_icu', sep_data=Sep_3, lab_demo=lab_demo3,just_icu=True, icustays=icustays, stays_list=complete_stay_list)

with open('E:/Mimic_data/microbiol_fungal_dat_.pkl', 'wb') as handle:
    pickle.dump(microbiol_fungal_dat, handle, protocol=pickle.HIGHEST_PROTOCOL)

C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2441: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["charttime"] = microbiol_id["charttime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2442: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["storetime"] = microbiol_id["storetime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2443: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a 

C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2441: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["charttime"] = microbiol_id["charttime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2442: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["storetime"] = microbiol_id["storetime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2443: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a 

C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2441: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["charttime"] = microbiol_id["charttime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2442: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["storetime"] = microbiol_id["storetime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2443: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a 

C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2441: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["charttime"] = microbiol_id["charttime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2442: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["storetime"] = microbiol_id["storetime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2443: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a 

C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2441: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["charttime"] = microbiol_id["charttime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2442: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["storetime"] = microbiol_id["storetime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2443: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a 

...

C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2441: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["charttime"] = microbiol_id["charttime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2442: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["storetime"] = microbiol_id["storetime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2443: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a 

C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2441: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["charttime"] = microbiol_id["charttime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2442: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["storetime"] = microbiol_id["storetime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2443: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a 

C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2441: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["charttime"] = microbiol_id["charttime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2442: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["storetime"] = microbiol_id["storetime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2443: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a 

C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2441: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["charttime"] = microbiol_id["charttime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2442: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["storetime"] = microbiol_id["storetime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2443: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a 

C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2441: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["charttime"] = microbiol_id["charttime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2442: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  microbiol_id["storetime"] = microbiol_id["storetime"]-start
C:\Users\wendland\AppData\Local\Temp\ipykernel_12568\1269212923.py:2443: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a 